In [1]:
import os
import sys
import json
import re
import socket
import ssl
import pandas as pd
import smtplib as smtp
import requests
from pandas.io.json import json_normalize
from urllib.request import Request, urlopen, URLError, HTTPError, ProxyHandler, build_opener, install_opener
from urllib.parse import quote, urlsplit, urlunsplit, urlencode
from random import randint
from time import sleep
from bs4 import BeautifulSoup

In [2]:
USER_AGENT = 'Mozilla/5.0 (Windows NT 6.1; WOW64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/74.0.3729.169 YaBrowser/19.6.1.153 Yowser/2.5 Safari/537.36'
PROXIES = {'https': 'https://37.203.246.48:42911'}
MIN_TIME_SLEEP = 1
MAX_TIME_SLEEP = 5
MAX_COUNTS = 5
TIMEOUT = 10

In [3]:
def get_content(url_page, timeout, proxies, file=False):
    counts = 0
    content = None
    while counts < MAX_COUNTS:
        try:
            request = Request(url_page)
            request.add_header('User-Agent', USER_AGENT)
            proxy_support = ProxyHandler(proxies)
            opener = build_opener(proxy_support)
            install_opener(opener)
            context = ssl._create_unverified_context()
            response = urlopen(request, context=context, timeout=timeout)
            if file:
                content = response.read()
            else:
                content =  response.read().decode(response.headers.get_content_charset())
            break
        except URLError as e:
            counts += 1
            print('URLError | ', url_page, ' | ', e, ' | counts: ', counts)
            sleep(randint(counts * MIN_TIME_SLEEP, counts * MAX_TIME_SLEEP))
        except HTTPError as e:
            counts += 1
            print('HTTPError | ', url_page, ' | ', e, ' | counts: ', counts)
            sleep(randint(counts * MIN_TIME_SLEEP, counts * MAX_TIME_SLEEP))
        except socket.timeout as e:
            counts += 1
            print('socket timeout | ', url_page, ' | ', e, ' | counts: ', counts)
            sleep(randint(counts * MIN_TIME_SLEEP, counts * MAX_TIME_SLEEP))
    return content

In [5]:
url_cld = 'https://1fnl.ru/champioship/results/'
html = get_content(url_cld, TIMEOUT, PROXIES)
soup = BeautifulSoup(html, 'lxml')

In [9]:
soup.find_all('div', {'class': 'arhive-monthes'})[2]

<div class="arhive-monthes">
<a href="/champioship/results/639/640/" title="1-Й КРУГ">1-Й КРУГ</a>|                                            <a href="/champioship/results/639/641/" title="2-Й КРУГ">2-Й КРУГ</a>
</div>

In [10]:
soup.find_all('div', {'class': 'arhive-year'})[2]

<div class="arhive-year"><a class="btn btn-primary" href="/champioship/results/639/" title="2018/2019">2018/2019</a></div>

In [19]:
def get_name_url(idx):
    df_urls = pd.read_csv('urls.csv', sep=';')
    url_tmt_plan = df_urls[df_urls['use'] == 1].iloc[idx]['url']
    site_name = df_urls[df_urls['use'] == 1].iloc[idx]['folder']
    return url_tmt_plan, site_name

In [21]:
idx = 0
url_tmt_plan, site_name = get_name_url(idx)
print('url: ', url_tmt_plan)
print('site name: ', site_name)

url:  https://ffrb.nagradion.ru/tournament-plan?start_date=&end_date=&status=-1&season_id=0&sport_id=0&competition_id=0&area_id=0&filter=
site name:  ffrb


In [4]:
CACHE_PATH = './data/{}/'.format(site_name)
if not os.path.exists(CACHE_PATH):
    os.makedirs(CACHE_PATH)
CACHE_PATH_PLNS = '{}_plns/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_PLNS):
    os.makedirs(CACHE_PATH_PLNS)
CACHE_PATH_PLNS_RAW = '{}_plns_raw/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_PLNS_RAW):
    os.makedirs(CACHE_PATH_PLNS_RAW)
CACHE_PATH_TMTS = '{}tmts/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_TMTS):
    os.makedirs(CACHE_PATH_TMTS)
CACHE_PATH_TMTS_RAW = '{}tmts_raw/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_TMTS_RAW):
    os.makedirs(CACHE_PATH_TMTS_RAW)
CACHE_PATH_GMS = '{}games/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_GMS):
    os.makedirs(CACHE_PATH_GMS)
CACHE_PATH_GMS_RAW = '{}games_raw/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_GMS_RAW):
    os.makedirs(CACHE_PATH_GMS_RAW)
CACHE_PATH_STMS = '{}stadiums/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_STMS):
    os.makedirs(CACHE_PATH_STMS)
CACHE_PATH_STMS_RAW = '{}stadiums_raw/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_STMS_RAW):
    os.makedirs(CACHE_PATH_STMS_RAW)
CACHE_PATH_PLRS = '{}players/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_PLRS):
    os.makedirs(CACHE_PATH_PLRS)
CACHE_PATH_PLRS_RAW = '{}players_raw/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_PLRS_RAW):
    os.makedirs(CACHE_PATH_PLRS_RAW)
CACHE_PATH_RFRS = '{}referees/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_RFRS):
    os.makedirs(CACHE_PATH_RFRS)
CACHE_PATH_RFRS_RAW = '{}referees_raw/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_RFRS_RAW):
    os.makedirs(CACHE_PATH_RFRS_RAW)
CACHE_PATH_OFLS = '{}officials/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_OFLS):
    os.makedirs(CACHE_PATH_OFLS)
CACHE_PATH_OFLS_RAW = '{}officials_raw/'.format(CACHE_PATH)
if not os.path.exists(CACHE_PATH_OFLS_RAW):
    os.makedirs(CACHE_PATH_OFLS_RAW)

site name:  ffrt


# All tournaments

In [5]:
html = get_content(url_tmt_plan, TIMEOUT, PROXIES)
file_name = '{}{}_tmt_plan.html'.format(CACHE_PATH_PLNS_RAW, site_name)
with open(file_name, 'w', encoding='utf-8') as file:
    file.write(str(html))
with open(file_name, 'r', encoding='utf-8') as file:
    html = file.read()
soup = BeautifulSoup(html, 'html.parser')
table_tmt_plan = soup.find('table', {'class': 'table table-striped'})
list_data_tmt_plan = []
for row in table_tmt_plan.find_all('tr', {'class': ''}):
    dict_row = {}
    if row.find_all('th'):
        headers = ['{}_{}'.format(str(i), x.text.strip()) for i, x in enumerate(row.find_all('th'))]
    else:
        try:
            cols = row.find_all('td')
            for k, v in zip(headers, cols):
                dict_row.update({k: ' '.join(v.text.split())})
                if v.find('a', href=True):
                    k = k + '_href'
                    dict_row.update({k: v.find('a', href=True)['href']})
            list_data_tmt_plan.append(dict_row)
        except:
            print('no correct data')
file_name = '{}{}_tmt_plan.txt'.format(CACHE_PATH_PLNS, site_name)
with open(file_name, 'w') as file:
    json.dump(list_data_tmt_plan, file)
print('data saved to: ', file_name)

data saved to:  ./data/ffrt/_plns/ffrt_tmt_plan.txt


In [6]:
print('total tournaments: ', len(list_data_tmt_plan))
print('tournament example: ', list_data_tmt_plan[0])

total tournaments:  255
tournament example:  {'0_': '1', '1_Название': 'Кубок Республики Татарстан по футболу 2019 года Юноши 2006 г.р.', '1_Название_href': 'http://ffrt.ru/tournament15122', '2_Вид спорта': 'Футбол', '3_Сезон': '2019 год', '4_Соревнование': 'Кубок РТ среди юношей', '5_Сроки проведения': 'с 27.05.2019 по 08.09.2019', '6_Статус': 'Завершён', '7_': 'Таблица и статистика', '7__href': 'https://ffrt.ru/tournament15122/table'}


# Tours and games lists by tournaments

In [10]:
start_index = len(os.listdir(CACHE_PATH_TMTS))
for i_tmt, tmt_from_plan in enumerate(list_data_tmt_plan[start_index:]):
    url_tmt = '{}{}'.format(tmt_from_plan['1_Название_href'], '/calendar')
    print(start_index + i_tmt, 'processing:', url_tmt)
    tmt_from_plan_id = url_tmt[url_tmt.find('.ru/') + len('.ru/'):url_tmt.find('/calendar')]
    html = get_content(url_tmt, TIMEOUT, PROXIES)
    file_name = '{}{}_tmt_id_{}.html'.format(CACHE_PATH_TMTS_RAW, site_name, tmt_from_plan_id)
    with open(file_name, 'w', encoding='utf-8') as file:
        file.write(str(html))
    with open(file_name, 'r', encoding='utf-8') as file:
        html = file.read()
    soup = BeautifulSoup(html, 'html.parser')
    dict_data_tmt = {}
    for tmt_tour, table_tmt_tour in zip([x.text.strip() for x in soup.find_all('h2')], 
                                        soup.find_all('table', {'class': 'oneTourSchedule table table-striped'})):
        dict_data_tmt_tour = []
        for row in table_tmt_tour.find_all('tr'):
            dict_row = {}
            if row.find_all('th'):
                headers = []
                for i, x in enumerate(row.find_all('th')):
                    headers.append('{}_{}'.format(str(i), x.text.strip()))
                    try:
                        for j in range(int(x['colspan']) - 1):
                            headers.append('{}_{}_{}'.format(str(i), x.text.strip(), j))
                    except:
                        pass
            else:
                try:
                    cols = row.find_all('td')
                    if len(row.find_all('td')) > len(headers):
                        headers.extend(['{}_'.format(i) for i in range(len(headers), len(row.find_all('td')))])
                    for k, v in zip(headers, cols):
                        dict_row.update({k: ' '.join(v.text.split())})
                        if v.find_all('a', href=True):
                            for i, href_i in enumerate(v.find_all('a', href=True)):
                                k = '{}_href_{}'.format(k, i)
                                dict_row.update({k: href_i['href']})
                    dict_data_tmt_tour.append(dict_row)
                except:
                    print('no correct data')
        #print('part done: ', tmt_tour)
        dict_data_tmt.update({tmt_tour: dict_data_tmt_tour})
    file_name = '{}{}_tmt_id_{}.txt'.format(CACHE_PATH_TMTS, site_name, tmt_from_plan_id)
    with open(file_name, 'w') as file:
        json.dump(dict_data_tmt, file)
    print(start_index + i_tmt, 'done: ', file_name)
    sleep(randint(MIN_TIME_SLEEP, MAX_TIME_SLEEP))

203 processing: http://ffrt.ru/tournament1887/calendar
203 done:  ./data/ffrt/tmts/ffrt_tmt_id_tournament1887.txt
204 processing: http://ffrt.ru/tournament1756/calendar
204 done:  ./data/ffrt/tmts/ffrt_tmt_id_tournament1756.txt
205 processing: http://ffrt.ru/tournament2614/calendar
205 done:  ./data/ffrt/tmts/ffrt_tmt_id_tournament2614.txt
206 processing: http://ffrt.ru/tournament1588/calendar
206 done:  ./data/ffrt/tmts/ffrt_tmt_id_tournament1588.txt
207 processing: http://ffrt.ru/tournament1578/calendar
207 done:  ./data/ffrt/tmts/ffrt_tmt_id_tournament1578.txt
208 processing: http://ffrt.ru/tournament1613/calendar
208 done:  ./data/ffrt/tmts/ffrt_tmt_id_tournament1613.txt
209 processing: http://ffrt.ru/tournament1614/calendar
209 done:  ./data/ffrt/tmts/ffrt_tmt_id_tournament1614.txt
210 processing: http://ffrt.ru/tournament1615/calendar
210 done:  ./data/ffrt/tmts/ffrt_tmt_id_tournament1615.txt
211 processing: http://ffrt.ru/tournament1616/calendar
211 done:  ./data/ffrt/tmts/ffrt_

In [11]:
print('example of tournament tours: ', dict_data_tmt.keys())
print('example of games / matches in tour: ', len(dict_data_tmt[list(dict_data_tmt.keys())[0]]))
print('example of one game / match: ', dict_data_tmt[list(dict_data_tmt.keys())[0]][0])

example of tournament tours:  dict_keys(['1 тур', '2 тур', '3 тур', '4 тур', '5 тур'])
example of games / matches in tour:  2
example of one game / match:  {'0_#': '1', '1_Дата': '21.03.2018 Ср', '1_Дата_0': '15:00', '2_Команды': 'Строитель (Набережные Челны) — Компонент (Набережные Челны)', '2_Команды_href_0': 'https://ffrt.ru/tournament8949/team/72839/players', '2_Команды_href_0_href_1': '#', '2_Команды_href_0_href_1_href_2': 'https://ffrt.ru/tournament8949/team/72836/players', '3_Счёт': '2:0', '4_Стадион': 'ст.КАМАЗ Набережные Челны', '4_Стадион_href_0': '#', '5_': 'отчёты (2) |0', '5__href_0': 'https://ffrt.ru/tournament8949/match/597079', '5__href_0_href_1': 'https://ffrt.ru/tournament8949/match/597079'}


# By single game

In [12]:
tmt_files = os.listdir(CACHE_PATH_TMTS)
url_games = []
url_teams = []
for i_file, tmt_file_name in enumerate(tmt_files):
    print(i_file, 'processing: ', tmt_file_name)
    with open('{}/{}'.format(CACHE_PATH_TMTS, tmt_file_name)) as file:
        data_json = json.load(file)
    for key in data_json.keys():
        for game in data_json[key]:
            url_games.extend([v for k, v in game.items() if ('href' in k) and ('match' in v)])
            url_teams.extend([v for k, v in game.items() if ('href' in k) and ('team' in v)])
print('games: ', len(url_games), ' | unique games: ', len(set(url_games)))
print('teams: ', len(url_teams), ' | unique teams: ', len(set(url_teams)))
url_games = list(set(url_games))
url_teams = list(set(url_teams))

0 processing:  ffrt_tmt_id_tournament10050.txt
1 processing:  ffrt_tmt_id_tournament10051.txt
2 processing:  ffrt_tmt_id_tournament10075.txt
3 processing:  ffrt_tmt_id_tournament10121.txt
4 processing:  ffrt_tmt_id_tournament10122.txt
5 processing:  ffrt_tmt_id_tournament10123.txt
6 processing:  ffrt_tmt_id_tournament10154.txt
7 processing:  ffrt_tmt_id_tournament10176.txt
8 processing:  ffrt_tmt_id_tournament10317.txt
9 processing:  ffrt_tmt_id_tournament10374.txt
10 processing:  ffrt_tmt_id_tournament10375.txt
11 processing:  ffrt_tmt_id_tournament11502.txt
12 processing:  ffrt_tmt_id_tournament12613.txt
13 processing:  ffrt_tmt_id_tournament12616.txt
14 processing:  ffrt_tmt_id_tournament12986.txt
15 processing:  ffrt_tmt_id_tournament12998.txt
16 processing:  ffrt_tmt_id_tournament13061.txt
17 processing:  ffrt_tmt_id_tournament13137.txt
18 processing:  ffrt_tmt_id_tournament13223.txt
19 processing:  ffrt_tmt_id_tournament13351.txt
20 processing:  ffrt_tmt_id_tournament13359.txt
21

204 processing:  ffrt_tmt_id_tournament7054.txt
205 processing:  ffrt_tmt_id_tournament7120.txt
206 processing:  ffrt_tmt_id_tournament7122.txt
207 processing:  ffrt_tmt_id_tournament7190.txt
208 processing:  ffrt_tmt_id_tournament7191.txt
209 processing:  ffrt_tmt_id_tournament7192.txt
210 processing:  ffrt_tmt_id_tournament7193.txt
211 processing:  ffrt_tmt_id_tournament7194.txt
212 processing:  ffrt_tmt_id_tournament7195.txt
213 processing:  ffrt_tmt_id_tournament7196.txt
214 processing:  ffrt_tmt_id_tournament7197.txt
215 processing:  ffrt_tmt_id_tournament7198.txt
216 processing:  ffrt_tmt_id_tournament7199.txt
217 processing:  ffrt_tmt_id_tournament7363.txt
218 processing:  ffrt_tmt_id_tournament7404.txt
219 processing:  ffrt_tmt_id_tournament7454.txt
220 processing:  ffrt_tmt_id_tournament7463.txt
221 processing:  ffrt_tmt_id_tournament8197.txt
222 processing:  ffrt_tmt_id_tournament8914.txt
223 processing:  ffrt_tmt_id_tournament8931.txt
224 processing:  ffrt_tmt_id_tournament8

In [15]:
start_index = len(os.listdir(CACHE_PATH_GMS))
for url_num, url_game in enumerate(url_games[start_index:]):
    print(start_index + url_num, 'processing:', url_game)
    game_data = {}
    game_id = url_game[url_game.find('/match') + len('/match') + 1:]
    html = get_content(url_game, TIMEOUT, PROXIES)
    file_name = '{}{}_game_id_{}.html'.format(CACHE_PATH_GMS_RAW, site_name, game_id)
    with open(file_name, 'w', encoding='utf-8') as file:
        file.write(str(html))
    with open(file_name, 'r', encoding='utf-8') as file:
        html = file.read()
    soup = BeautifulSoup(html, 'lxml')
    #---staduium info---
    try:
        game_data['стадион'] = soup.find('a', {'class': 'match-header__stadium'}).text.strip()
        game_data['стадион_href_0'] = soup.find('a', {'class': 'match-header__stadium'})['href']  
    except:
        print('error stadium href field')
    try:
        game_data['освещение'] = soup.find('i', {'class': 'fa fa-sun-o fa-fw'})['title']
        game_data['описание'] = ' '.join(soup.find('div', {'class': 'panel-heading'}).text.split())
    except:
        print('error stadium description field')
    #---inner tables---
    tables_names = ['overall', 'team_1', 'team_2', 'referees']
    if len(soup.find_all('table')) >= 2:
        for table_name, table in zip(tables_names, soup.find_all('table')):
            table_data = []
            if table.find('thead'):
                thead = []
                for i_th, th in enumerate(table.find('thead').find_all('th')):
                    #---ATTENTION HARDCODED STUFF BELOW---
                    if table_name == 'overall':
                        if th.text != '':
                            thead.append('{}_{}'.format(i_th, th.text))
                        else:
                            pass
                    #---END OF HARDCODE---
                    else:
                        thead.append('{}_{}'.format(i_th, th.text))
                back_up = False
                for body in table.find_all('tbody'):
                    for row in body.find_all('tr'):
                        row_data = {}
                        if row.find('th'):
                            inn_thead = '{}_{}'.format(0, row.find('th').text)
                            #---ATTENTION HARDCODED STUFF BELOW---
                            if 'запас' in inn_thead:
                                back_up = True
                            #---END OF HARDCODE---
                        else:
                            inn_thead = None
                        if len(row.find_all('td')) > len(thead):
                            thead.extend(['{}_'.format(i) for i in range(len(thead), len(row.find_all('td')))])
                        for i_td, td in enumerate(row.find_all('td')):
                            row_data[thead[i_td]] = ' '.join(td.text.split())
                            if td.find_all('a', href=True):
                                for i_href, href in enumerate(td.find_all('a', href=True)):
                                    key = '{}_href_{}'.format(thead[i_td], i_href)
                                    row_data.update({key: href['href']})
                            #---ATTENTION HARDCODED STUFF BELOW---
                            if td.find('div', {'class': 'pull-right foul-card yellow-card'}):
                                row_data.update({'yellow-card': td.find('div', {'class': 'pull-right foul-card yellow-card'})['title']})
                            if td.find('div', {'class': 'pull-right foul-card red-card'}):
                                row_data.update({'red-card': td.find('div', {'class': 'pull-right foul-card red-card'})['title']})
                            if back_up:
                                row_data.update({'{}_запасные'.format(len(thead)): back_up})
                            #---END OF HARDCODE---
                        if inn_thead:
                            table_data.append({inn_thead: row_data})
                        else:
                            table_data.append(row_data)
            else:
                row_data = {}
                for row in table.find('tbody').find_all('tr'):
                    for i_td, td in enumerate(row.find_all('td')):
                        if row.find_all('th'):
                            key = str(i_td) + '_' + ' '.join(row.find('th').text.split())
                            row_data[key] = ' '.join(td.text.split())
                            if td.find_all('a', href=True):
                                for i_href, href in enumerate(td.find_all('a', href=True)):
                                    key_href = '{}_href_{}'.format(key, i_href)
                                    row_data.update({key_href: href['href']})
                table_data.append(row_data)
            game_data[table_name] = table_data
    #---write to file---
    file_name = '{}{}_game_id_{}.txt'.format(CACHE_PATH_GMS, site_name, game_id)
    with open(file_name, 'w') as file:
        json.dump(game_data, file)
    print(start_index + url_num, 'done: ', file_name)
    sleep(randint(MIN_TIME_SLEEP, MAX_TIME_SLEEP))

6433 processing: https://ffrt.ru/tournament15131/match/1035682
error stadium description field
6433 done:  ./data/ffrt/games/ffrt_game_id_1035682.txt
6434 processing: https://ffrt.ru/tournament3147/match/307855
error stadium description field
6434 done:  ./data/ffrt/games/ffrt_game_id_307855.txt
6435 processing: https://ffrt.ru/tournament13829/match/830936
6435 done:  ./data/ffrt/games/ffrt_game_id_830936.txt
6436 processing: https://ffrt.ru/tournament1882/match/171184
error stadium description field
6436 done:  ./data/ffrt/games/ffrt_game_id_171184.txt
6437 processing: https://ffrt.ru/tournament3110/match/303759
error stadium description field
6437 done:  ./data/ffrt/games/ffrt_game_id_303759.txt
6438 processing: https://ffrt.ru/tournament9094/match/623536
6438 done:  ./data/ffrt/games/ffrt_game_id_623536.txt
6439 processing: https://ffrt.ru/tournament2082/match/245822
error stadium description field
6439 done:  ./data/ffrt/games/ffrt_game_id_245822.txt
6440 processing: https://ffrt.r

6495 processing: https://ffrt.ru/tournament15421/match/1029586
error stadium description field
6495 done:  ./data/ffrt/games/ffrt_game_id_1029586.txt
6496 processing: https://ffrt.ru/tournament8934/match/594114
6496 done:  ./data/ffrt/games/ffrt_game_id_594114.txt
6497 processing: https://ffrt.ru/tournament13223/match/803868
error stadium description field
6497 done:  ./data/ffrt/games/ffrt_game_id_803868.txt
6498 processing: https://ffrt.ru/tournament14989/match/972127
error stadium description field
6498 done:  ./data/ffrt/games/ffrt_game_id_972127.txt
6499 processing: https://ffrt.ru/tournament9265/match/641691
6499 done:  ./data/ffrt/games/ffrt_game_id_641691.txt
6500 processing: https://ffrt.ru/tournament16665/match/1099790
error stadium description field
6500 done:  ./data/ffrt/games/ffrt_game_id_1099790.txt
6501 processing: https://ffrt.ru/tournament3090/match/300511
error stadium description field
6501 done:  ./data/ffrt/games/ffrt_game_id_300511.txt
6502 processing: https://ff

6555 processing: https://ffrt.ru/tournament9265/match/641737
6555 done:  ./data/ffrt/games/ffrt_game_id_641737.txt
6556 processing: https://ffrt.ru/tournament10051/match/681932
error stadium description field
6556 done:  ./data/ffrt/games/ffrt_game_id_681932.txt
6557 processing: https://ffrt.ru/tournament1882/match/171183
error stadium description field
6557 done:  ./data/ffrt/games/ffrt_game_id_171183.txt
6558 processing: https://ffrt.ru/tournament13818/match/982017
6558 done:  ./data/ffrt/games/ffrt_game_id_982017.txt
6559 processing: https://ffrt.ru/tournament8978/match/635138
6559 done:  ./data/ffrt/games/ffrt_game_id_635138.txt
6560 processing: https://ffrt.ru/tournament13830/match/830999
6560 done:  ./data/ffrt/games/ffrt_game_id_830999.txt
6561 processing: https://ffrt.ru/tournament3191/match/331490
error stadium description field
6561 done:  ./data/ffrt/games/ffrt_game_id_331490.txt
6562 processing: https://ffrt.ru/tournament15132/match/999703
6562 done:  ./data/ffrt/games/ffrt

6618 processing: https://ffrt.ru/tournament13522/match/806994
error stadium description field
6618 done:  ./data/ffrt/games/ffrt_game_id_806994.txt
6619 processing: https://ffrt.ru/tournament10050/match/681921
error stadium description field
6619 done:  ./data/ffrt/games/ffrt_game_id_681921.txt
6620 processing: https://ffrt.ru/tournament13446/match/795976
6620 done:  ./data/ffrt/games/ffrt_game_id_795976.txt
6621 processing: https://ffrt.ru/tournament15420/match/1054721
error stadium description field
6621 done:  ./data/ffrt/games/ffrt_game_id_1054721.txt
6622 processing: https://ffrt.ru/tournament3526/match/345462
6622 done:  ./data/ffrt/games/ffrt_game_id_345462.txt
6623 processing: https://ffrt.ru/tournament1755/match/153173
error stadium description field
6623 done:  ./data/ffrt/games/ffrt_game_id_153173.txt
6624 processing: https://ffrt.ru/tournament3895/match/386865
error stadium description field
6624 done:  ./data/ffrt/games/ffrt_game_id_386865.txt
6625 processing: https://ffrt

6680 done:  ./data/ffrt/games/ffrt_game_id_431035.txt
6681 processing: https://ffrt.ru/tournament9230/match/648658
error stadium description field
6681 done:  ./data/ffrt/games/ffrt_game_id_648658.txt
6682 processing: https://ffrt.ru/tournament3183/match/311188
6682 done:  ./data/ffrt/games/ffrt_game_id_311188.txt
6683 processing: https://ffrt.ru/tournament3651/match/356431
6683 done:  ./data/ffrt/games/ffrt_game_id_356431.txt
6684 processing: https://ffrt.ru/tournament1578/match/125729
error stadium description field
6684 done:  ./data/ffrt/games/ffrt_game_id_125729.txt
6685 processing: https://ffrt.ru/tournament3527/match/345417
6685 done:  ./data/ffrt/games/ffrt_game_id_345417.txt
6686 processing: https://ffrt.ru/tournament4192/match/431086
error stadium description field
6686 done:  ./data/ffrt/games/ffrt_game_id_431086.txt
6687 processing: https://ffrt.ru/tournament4361/match/429094
6687 done:  ./data/ffrt/games/ffrt_game_id_429094.txt
6688 processing: https://ffrt.ru/tournament12

...

8884 processing: https://ffrt.ru/tournament13850/match/833500
8884 done:  ./data/ffrt/games/ffrt_game_id_833500.txt
8885 processing: https://ffrt.ru/tournament3651/match/356477
8885 done:  ./data/ffrt/games/ffrt_game_id_356477.txt
8886 processing: https://ffrt.ru/tournament14855/match/900961
error stadium description field
8886 done:  ./data/ffrt/games/ffrt_game_id_900961.txt
8887 processing: https://ffrt.ru/tournament15029/match/979035
error stadium description field
8887 done:  ./data/ffrt/games/ffrt_game_id_979035.txt
8888 processing: https://ffrt.ru/tournament2090/match/207413
error stadium description field
8888 done:  ./data/ffrt/games/ffrt_game_id_207413.txt
8889 processing: https://ffrt.ru/tournament6949/match/498950
error stadium description field
8889 done:  ./data/ffrt/games/ffrt_game_id_498950.txt
8890 processing: https://ffrt.ru/tournament16229/match/1066398
error stadium description field
8890 done:  ./data/ffrt/games/ffrt_game_id_1066398.txt
8891 processing: https://ffrt

8947 processing: https://ffrt.ru/tournament8980/match/636609
8947 done:  ./data/ffrt/games/ffrt_game_id_636609.txt
8948 processing: https://ffrt.ru/tournament15044/match/1003470
8948 done:  ./data/ffrt/games/ffrt_game_id_1003470.txt
8949 processing: https://ffrt.ru/tournament3135/match/307264
error stadium description field
8949 done:  ./data/ffrt/games/ffrt_game_id_307264.txt
8950 processing: https://ffrt.ru/tournament9224/match/644099
error stadium description field
8950 done:  ./data/ffrt/games/ffrt_game_id_644099.txt
8951 processing: https://ffrt.ru/tournament8952/match/602287
error stadium description field
8951 done:  ./data/ffrt/games/ffrt_game_id_602287.txt
8952 processing: https://ffrt.ru/tournament2090/match/207390
error stadium description field
8952 done:  ./data/ffrt/games/ffrt_game_id_207390.txt
8953 processing: https://ffrt.ru/tournament8980/match/636510
8953 done:  ./data/ffrt/games/ffrt_game_id_636510.txt
8954 processing: https://ffrt.ru/tournament13829/match/830949
89

error stadium description field
9008 done:  ./data/ffrt/games/ffrt_game_id_153118.txt
9009 processing: https://ffrt.ru/tournament3952/match/393483
error stadium description field
9009 done:  ./data/ffrt/games/ffrt_game_id_393483.txt
9010 processing: https://ffrt.ru/tournament9224/match/701047
9010 done:  ./data/ffrt/games/ffrt_game_id_701047.txt
9011 processing: https://ffrt.ru/tournament4019/match/402163
9011 done:  ./data/ffrt/games/ffrt_game_id_402163.txt
9012 processing: https://ffrt.ru/tournament9095/match/623807
9012 done:  ./data/ffrt/games/ffrt_game_id_623807.txt
9013 processing: https://ffrt.ru/tournament4085/match/450119
9013 done:  ./data/ffrt/games/ffrt_game_id_450119.txt
9014 processing: https://ffrt.ru/tournament15043/match/1002525
9014 done:  ./data/ffrt/games/ffrt_game_id_1002525.txt
9015 processing: https://ffrt.ru/tournament1588/match/129490
error stadium description field
9015 done:  ./data/ffrt/games/ffrt_game_id_129490.txt
9016 processing: https://ffrt.ru/tournamen

9071 processing: https://ffrt.ru/tournament13427/match/807655
error stadium description field
9071 done:  ./data/ffrt/games/ffrt_game_id_807655.txt
9072 processing: https://ffrt.ru/tournament3638/match/354461
9072 done:  ./data/ffrt/games/ffrt_game_id_354461.txt
9073 processing: https://ffrt.ru/tournament2089/match/196376
error stadium description field
9073 done:  ./data/ffrt/games/ffrt_game_id_196376.txt
9074 processing: https://ffrt.ru/tournament4255/match/424255
error stadium description field
9074 done:  ./data/ffrt/games/ffrt_game_id_424255.txt
9075 processing: https://ffrt.ru/tournament1634/match/131004
error stadium description field
9075 done:  ./data/ffrt/games/ffrt_game_id_131004.txt
9076 processing: https://ffrt.ru/tournament13830/match/830995
9076 done:  ./data/ffrt/games/ffrt_game_id_830995.txt
9077 processing: https://ffrt.ru/tournament1588/match/127549
error stadium description field
9077 done:  ./data/ffrt/games/ffrt_game_id_127549.txt
9078 processing: https://ffrt.ru/

error stadium description field
9134 done:  ./data/ffrt/games/ffrt_game_id_176149.txt
9135 processing: https://ffrt.ru/tournament3526/match/345473
9135 done:  ./data/ffrt/games/ffrt_game_id_345473.txt
9136 processing: https://ffrt.ru/tournament1887/match/237281
error stadium description field
9136 done:  ./data/ffrt/games/ffrt_game_id_237281.txt
9137 processing: https://ffrt.ru/tournament13818/match/982010
9137 done:  ./data/ffrt/games/ffrt_game_id_982010.txt
9138 processing: https://ffrt.ru/tournament15047/match/977071
error stadium description field
9138 done:  ./data/ffrt/games/ffrt_game_id_977071.txt
9139 processing: https://ffrt.ru/tournament2082/match/203424
error stadium description field
9139 done:  ./data/ffrt/games/ffrt_game_id_203424.txt
9140 processing: https://ffrt.ru/tournament6798/match/478519
error stadium description field
9140 done:  ./data/ffrt/games/ffrt_game_id_478519.txt
9141 processing: https://ffrt.ru/tournament15047/match/977113
9141 done:  ./data/ffrt/games/ff

## By single stadium

In [6]:
gms_files = os.listdir(CACHE_PATH_GMS)
url_stadiums = []
for gms_file_name in gms_files:
    with open('{}/{}'.format(CACHE_PATH_GMS, gms_file_name)) as file:
        data_json = json.load(file)
    for key, value in data_json.items():
        if 'href' in key:
            url_stadiums.append(value)
print('games processed: ', len(gms_files), 
      ' | found stadium urls: ', len(url_stadiums),
      ' | found unique stadium urls: ', len(set(url_stadiums)))
print('examples of stadium urls: ', url_stadiums[:3])
url_stadiums = list(set(url_stadiums))

games processed:  9150  | found stadium urls:  8990  | found unique stadium urls:  1054
examples of stadium urls:  ['https://ffrt.ru/tournament15043/stadiums/stadium/1046', 'https://ffrt.ru/tournament15043/stadiums/stadium/1046', 'https://ffrt.ru/tournament15043/stadiums/stadium/1045']


In [17]:
start_index = len(os.listdir(CACHE_PATH_STMS))
for i_stm, url_stm in enumerate(url_stadiums[start_index:]):
    print(i_stm + start_index, 'processing: ', url_stm)
    html = get_content(url_stm, TIMEOUT, PROXIES)
    stm_id = url_stm[url_stm.find('stadium/') + len('stadium/'):]
    file_name = '{}{}_stadium_id_{}.html'.format(CACHE_PATH_STMS_RAW, site_name, stm_id)
    with open(file_name, 'w', encoding='utf-8') as file:
        file.write(str(html))
    with open(file_name, 'r', encoding='utf-8') as file:
        html = file.read()
    soup = BeautifulSoup(html, 'lxml')
    stm_data = {}
    if soup.find_all('table', {'class': 'table'}):
        for row in soup.find_all('table', {'class': 'table'})[0].find_all('tr'):
            if row.find_all('td'):
                td = row.find_all('td')
                stm_data[td[0].text] = td[1].text
    else:
        print('no stadium table: ', url_stm)
    if soup.find_all('div', {'class': 'list-group'}):
        clubs = []
        for a in soup.find_all('div', {'class': 'list-group'})[0].find_all('a'):
            clubs.append({a.text: a['href']})
        stm_data['Клубы'] = clubs
    else:
        print('no clubs for stadium: ', url_stm)
    file_name = '{}{}_stadium_id_{}.txt'.format(CACHE_PATH_STMS, site_name, stm_id)
    with open(file_name, 'w') as file:
        json.dump(stm_data, file)
    print(i_stm + start_index, 'done: ', file_name)
    sleep(randint(MIN_TIME_SLEEP, MAX_TIME_SLEEP))

0 processing:  https://ffrt.ru/tournament10374/stadiums/stadium/1111
no clubs for stadium:  https://ffrt.ru/tournament10374/stadiums/stadium/1111
0 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1111.txt
1 processing:  https://ffrt.ru/tournament4085/stadiums/stadium/1059
1 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1059.txt
2 processing:  https://ffrt.ru/tournament3651/stadiums/stadium/1498
2 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1498.txt
3 processing:  https://ffrt.ru/tournament9232/stadiums/stadium/1056
3 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1056.txt
4 processing:  https://ffrt.ru/tournament7196/stadiums/stadium/1046
4 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1046.txt
5 processing:  https://ffrt.ru/tournament3110/stadiums/stadium/1922
no clubs for stadium:  https://ffrt.ru/tournament3110/stadiums/stadium/1922
5 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1922.txt
6 processing:  https://ffrt.ru/tournament10051/stadiums/stadium/1049
6 done:  ./data/ffrt/stadiums/ffrt_stad

53 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1718.txt
54 processing:  https://ffrt.ru/tournament13825/stadiums/stadium/1045
54 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1045.txt
55 processing:  https://ffrt.ru/tournament9265/stadiums/stadium/1049
55 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1049.txt
56 processing:  https://ffrt.ru/tournament4359/stadiums/stadium/1049
56 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1049.txt
57 processing:  https://ffrt.ru/tournament13830/stadiums/stadium/1042
57 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1042.txt
58 processing:  https://ffrt.ru/tournament13364/stadiums/stadium/1043
58 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1043.txt
59 processing:  https://ffrt.ru/tournament9176/stadiums/stadium/1064
no clubs for stadium:  https://ffrt.ru/tournament9176/stadiums/stadium/1064
59 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1064.txt
60 processing:  https://ffrt.ru/tournament3639/stadiums/stadium/1045
60 done:  ./data/ffrt/stadiums/ffrt_stadium_id

112 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1105.txt
113 processing:  https://ffrt.ru/tournament8938/stadiums/stadium/1105
113 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1105.txt
114 processing:  https://ffrt.ru/tournament13522/stadiums/stadium/1047
114 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1047.txt
115 processing:  https://ffrt.ru/tournament3529/stadiums/stadium/1042
115 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1042.txt
116 processing:  https://ffrt.ru/tournament15418/stadiums/stadium/1718
116 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1718.txt
117 processing:  https://ffrt.ru/tournament2082/stadiums/stadium/1059
117 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1059.txt
118 processing:  https://ffrt.ru/tournament15047/stadiums/stadium/1067
no clubs for stadium:  https://ffrt.ru/tournament15047/stadiums/stadium/1067
118 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1067.txt
119 processing:  https://ffrt.ru/tournament15122/stadiums/stadium/1042
119 done:  ./data/ffrt/stadium

168 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1056.txt
169 processing:  https://ffrt.ru/tournament15131/stadiums/stadium/1045
169 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1045.txt
170 processing:  https://ffrt.ru/tournament1888/stadiums/stadium/1065
170 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1065.txt
171 processing:  https://ffrt.ru/tournament4085/stadiums/stadium/1056
171 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1056.txt
172 processing:  https://ffrt.ru/tournament9265/stadiums/stadium/1050
172 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1050.txt
173 processing:  https://ffrt.ru/tournament1889/stadiums/stadium/1043
173 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1043.txt
174 processing:  https://ffrt.ru/tournament7198/stadiums/stadium/2017
no clubs for stadium:  https://ffrt.ru/tournament7198/stadiums/stadium/2017
174 done:  ./data/ffrt/stadiums/ffrt_stadium_id_2017.txt
175 processing:  https://ffrt.ru/tournament3214/stadiums/stadium/2017
no clubs for stadium:  https://ffr

no clubs for stadium:  https://ffrt.ru/tournament4131/stadiums/stadium/2460
224 done:  ./data/ffrt/stadiums/ffrt_stadium_id_2460.txt
225 processing:  https://ffrt.ru/tournament3430/stadiums/stadium/1105
225 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1105.txt
226 processing:  https://ffrt.ru/tournament10317/stadiums/stadium/1049
226 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1049.txt
227 processing:  https://ffrt.ru/tournament7199/stadiums/stadium/2017
no clubs for stadium:  https://ffrt.ru/tournament7199/stadiums/stadium/2017
227 done:  ./data/ffrt/stadiums/ffrt_stadium_id_2017.txt
228 processing:  https://ffrt.ru/tournament9176/stadiums/stadium/1061
228 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1061.txt
229 processing:  https://ffrt.ru/tournament2118/stadiums/stadium/1523
no clubs for stadium:  https://ffrt.ru/tournament2118/stadiums/stadium/1523
229 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1523.txt
230 processing:  https://ffrt.ru/tournament8980/stadiums/stadium/1045
230 done:

...

797 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1042.txt
798 processing:  https://ffrt.ru/tournament3188/stadiums/stadium/1043
798 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1043.txt
799 processing:  https://ffrt.ru/tournament1883/stadiums/stadium/1042
799 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1042.txt
800 processing:  https://ffrt.ru/tournament1887/stadiums/stadium/1045
800 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1045.txt
801 processing:  https://ffrt.ru/tournament8938/stadiums/stadium/1047
801 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1047.txt
802 processing:  https://ffrt.ru/tournament2090/stadiums/stadium/1045
802 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1045.txt
803 processing:  https://ffrt.ru/tournament3988/stadiums/stadium/1046
803 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1046.txt
804 processing:  https://ffrt.ru/tournament3187/stadiums/stadium/1042
804 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1042.txt
805 processing:  https://ffrt.ru/tournament3520/stadiu

853 processing:  https://ffrt.ru/tournament9176/stadiums/stadium/1045
853 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1045.txt
854 processing:  https://ffrt.ru/tournament2395/stadiums/stadium/1566
854 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1566.txt
855 processing:  https://ffrt.ru/tournament3190/stadiums/stadium/1045
855 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1045.txt
856 processing:  https://ffrt.ru/tournament9160/stadiums/stadium/1042
856 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1042.txt
857 processing:  https://ffrt.ru/tournament8980/stadiums/stadium/3660
no clubs for stadium:  https://ffrt.ru/tournament8980/stadiums/stadium/3660
857 done:  ./data/ffrt/stadiums/ffrt_stadium_id_3660.txt
858 processing:  https://ffrt.ru/tournament9160/stadiums/stadium/1498
858 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1498.txt
859 processing:  https://ffrt.ru/tournament15132/stadiums/stadium/1046
859 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1046.txt
860 processing:  https://ffrt.ru/t

no clubs for stadium:  https://ffrt.ru/tournament16667/stadiums/stadium/1111
909 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1111.txt
910 processing:  https://ffrt.ru/tournament10176/stadiums/stadium/1049
910 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1049.txt
911 processing:  https://ffrt.ru/tournament15049/stadiums/stadium/1523
no clubs for stadium:  https://ffrt.ru/tournament15049/stadiums/stadium/1523
911 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1523.txt
912 processing:  https://ffrt.ru/tournament4352/stadiums/stadium/1061
912 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1061.txt
913 processing:  https://ffrt.ru/tournament3581/stadiums/stadium/1166
no clubs for stadium:  https://ffrt.ru/tournament3581/stadiums/stadium/1166
913 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1166.txt
914 processing:  https://ffrt.ru/tournament15122/stadiums/stadium/1061
914 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1061.txt
915 processing:  https://ffrt.ru/tournament13369/stadiums/stadium/1042
915 

962 processing:  https://ffrt.ru/tournament3640/stadiums/stadium/1043
962 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1043.txt
963 processing:  https://ffrt.ru/tournament15294/stadiums/stadium/1915
no clubs for stadium:  https://ffrt.ru/tournament15294/stadiums/stadium/1915
963 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1915.txt
964 processing:  https://ffrt.ru/tournament9173/stadiums/stadium/1753
964 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1753.txt
965 processing:  https://ffrt.ru/tournament1889/stadiums/stadium/1042
965 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1042.txt
966 processing:  https://ffrt.ru/tournament2521/stadiums/stadium/1045
966 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1045.txt
967 processing:  https://ffrt.ru/tournament3527/stadiums/stadium/1051
no clubs for stadium:  https://ffrt.ru/tournament3527/stadiums/stadium/1051
967 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1051.txt
968 processing:  https://ffrt.ru/tournament7054/stadiums/stadium/1919
no clubs for s

no clubs for stadium:  https://ffrt.ru/tournament15420/stadiums/stadium/2460
1016 done:  ./data/ffrt/stadiums/ffrt_stadium_id_2460.txt
1017 processing:  https://ffrt.ru/tournament1578/stadiums/stadium/1045
1017 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1045.txt
1018 processing:  https://ffrt.ru/tournament15129/stadiums/stadium/2589
no clubs for stadium:  https://ffrt.ru/tournament15129/stadiums/stadium/2589
1018 done:  ./data/ffrt/stadiums/ffrt_stadium_id_2589.txt
1019 processing:  https://ffrt.ru/tournament15131/stadiums/stadium/1042
1019 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1042.txt
1020 processing:  https://ffrt.ru/tournament9231/stadiums/stadium/1065
1020 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1065.txt
1021 processing:  https://ffrt.ru/tournament3327/stadiums/stadium/1042
1021 done:  ./data/ffrt/stadiums/ffrt_stadium_id_1042.txt
1022 processing:  https://ffrt.ru/tournament3528/stadiums/stadium/2589
no clubs for stadium:  https://ffrt.ru/tournament3528/stadiums/stadium

## By single player

In [7]:
plr_files = os.listdir(CACHE_PATH_GMS)
url_plrs = []
url_rfrs = []
url_ofls = []
for gms_file_name in gms_files:
    with open('{}/{}'.format(CACHE_PATH_GMS, gms_file_name)) as file:
        data_json = json.load(file)
    for key, value in data_json.items():
        if 'team' in key:
            for item in value:
                url_plrs.extend([v for k, v in item.items() if ('href' in k) and ('player' in v)])
                url_ofls.extend([v for k, v in item.items() if ('href' in k) and ('official' in v)])
        if 'referee' in key:
            for item in value:
                url_rfrs.extend([v for k, v in item.items() if 'href' in k])
print('games processed: ', len(gms_files), 
      ' | found player urls: ', len(url_plrs),
      ' | found unique player urls: ', len(set(url_plrs)))
print('examples of player urls: ', url_plrs[:3])
print('games processed: ', len(gms_files), 
      ' | found referee urls: ', len(url_rfrs),
      ' | found unique referee urls: ', len(set(url_rfrs)))
print('examples of player urls: ', url_rfrs[:3])
print('games processed: ', len(gms_files), 
      ' | found official urls: ', len(url_ofls),
      ' | found unique official urls: ', len(set(url_ofls)))
print('examples of official urls: ', url_ofls[:3])
url_plrs = list(set(url_plrs))
url_rfrs = list(set(url_rfrs))
url_ofls = list(set(url_ofls))

games processed:  9150  | found player urls:  211218  | found unique player urls:  32851
examples of player urls:  ['https://ffrt.ru/tournament15043/player/416548', 'https://ffrt.ru/tournament15043/player/190053', 'https://ffrt.ru/tournament15043/player/190536']
games processed:  9150  | found referee urls:  10796  | found unique referee urls:  2820
examples of player urls:  ['https://ffrt.ru/tournament15043/referee/87887', 'https://ffrt.ru/tournament15043/referee/194002', 'https://ffrt.ru/tournament15043/referee/87887']
games processed:  9150  | found official urls:  19831  | found unique official urls:  2758
examples of official urls:  ['https://ffrt.ru/tournament15043/official/190548', 'https://ffrt.ru/tournament15043/official/170322', 'https://ffrt.ru/tournament15043/official/192397']


In [23]:
start_index = len(os.listdir(CACHE_PATH_PLRS))
for i_plr, url_plr in enumerate(url_plrs[start_index:]):
    print(i_plr + start_index, 'processing: ', url_plr)
    html = get_content(url_plr, TIMEOUT, PROXIES)
    plr_id = url_plr[url_plr.find('player/') + len('player/'):]
    file_name = '{}{}_player_id_{}.html'.format(CACHE_PATH_PLRS_RAW, site_name, plr_id)
    with open(file_name, 'w', encoding='utf-8') as file:
        file.write(str(html))
    with open(file_name, 'r', encoding='utf-8') as file:
        html = file.read()
    soup = BeautifulSoup(html, 'lxml')
    plr_data = {}
    if soup.find_all('h1'):
        plr_data['Имя'] = soup.find_all('h1')[0].text 
    if soup.find_all('table', {'class': 'table'}):
            for row in soup.find_all('table', {'class': 'table'})[0].find_all('tr'):
                plr_data[row.find('th').text] = row.find('td').text
    header = []
    for cell in soup.find_all('div', {'class': 'st-tbl__cell'}, title=True):
        header.append(cell.text)
    plr_tmts = []
    for cell in soup.find_all('div', {'class': 'st-tbl__cell', 'data-sort-value': True}, title=False):
        if cell.find_all('div', {'class': 'plr-details__info'}):
            plr_data_tmt = {}
            plr_data_tmt_stats = {}
            header_count = 0
            tmt_name = ' '.join(cell.find('div', {'class': 'plr-details__info'}).find('a').text.split())
            tmt_href = cell.find('div', {'class': 'plr-details__info'}).find('a', href=True)
            plr_data_tmt['tournament'] = tmt_name
            plr_data_tmt['href'] = tmt_href['href']
        else:
            plr_data_tmt_stats[header[header_count]] = cell.text
            header_count += 1
        plr_data_tmt['stats'] = plr_data_tmt_stats
        plr_tmts.append(plr_data_tmt)
    plr_data['all stats'] = plr_tmts       
    #---write to file---
    file_name = '{}{}_player_id_{}.txt'.format(CACHE_PATH_PLRS, site_name, plr_id)
    #print(plr_data)
    with open(file_name, 'w') as file:
        json.dump(plr_data, file)
    print(i_plr + start_index, 'done: ', file_name)
    sleep(randint(MIN_TIME_SLEEP, MAX_TIME_SLEEP))

8967 processing:  https://ffrt.ru/tournament13830/player/146646
8967 done:  ./data/ffrt/players/ffrt_player_id_146646.txt
8968 processing:  https://ffrt.ru/tournament3580/player/184049
8968 done:  ./data/ffrt/players/ffrt_player_id_184049.txt
8969 processing:  https://ffrt.ru/tournament10075/player/183507
8969 done:  ./data/ffrt/players/ffrt_player_id_183507.txt
8970 processing:  https://ffrt.ru/tournament15122/player/186747
8970 done:  ./data/ffrt/players/ffrt_player_id_186747.txt
8971 processing:  https://ffrt.ru/tournament16665/player/222058
8971 done:  ./data/ffrt/players/ffrt_player_id_222058.txt
8972 processing:  https://ffrt.ru/tournament9097/player/315776
8972 done:  ./data/ffrt/players/ffrt_player_id_315776.txt
8973 processing:  https://ffrt.ru/tournament9231/player/316433
8973 done:  ./data/ffrt/players/ffrt_player_id_316433.txt
8974 processing:  https://ffrt.ru/tournament3526/player/147273
8974 done:  ./data/ffrt/players/ffrt_player_id_147273.txt
8975 processing:  https://ff

9034 done:  ./data/ffrt/players/ffrt_player_id_146642.txt
9035 processing:  https://ffrt.ru/tournament15029/player/202884
9035 done:  ./data/ffrt/players/ffrt_player_id_202884.txt
9036 processing:  https://ffrt.ru/tournament3894/player/194624
9036 done:  ./data/ffrt/players/ffrt_player_id_194624.txt
9037 processing:  https://ffrt.ru/tournament9952/player/306724
9037 done:  ./data/ffrt/players/ffrt_player_id_306724.txt
9038 processing:  https://ffrt.ru/tournament4414/player/183886
9038 done:  ./data/ffrt/players/ffrt_player_id_183886.txt
9039 processing:  https://ffrt.ru/tournament1639/player/113663
9039 done:  ./data/ffrt/players/ffrt_player_id_113663.txt
9040 processing:  https://ffrt.ru/tournament13446/player/148985
9040 done:  ./data/ffrt/players/ffrt_player_id_148985.txt
9041 processing:  https://ffrt.ru/tournament4087/player/174941
9041 done:  ./data/ffrt/players/ffrt_player_id_174941.txt
9042 processing:  https://ffrt.ru/tournament10375/player/223540
9042 done:  ./data/ffrt/playe

9102 processing:  https://ffrt.ru/tournament7190/player/117331
9102 done:  ./data/ffrt/players/ffrt_player_id_117331.txt
9103 processing:  https://ffrt.ru/tournament15044/player/259206
9103 done:  ./data/ffrt/players/ffrt_player_id_259206.txt
9104 processing:  https://ffrt.ru/tournament15043/player/173876
9104 done:  ./data/ffrt/players/ffrt_player_id_173876.txt
9105 processing:  https://ffrt.ru/tournament3651/player/194639
9105 done:  ./data/ffrt/players/ffrt_player_id_194639.txt
9106 processing:  https://ffrt.ru/tournament3526/player/179789
9106 done:  ./data/ffrt/players/ffrt_player_id_179789.txt
9107 processing:  https://ffrt.ru/tournament13829/player/306850
9107 done:  ./data/ffrt/players/ffrt_player_id_306850.txt
9108 processing:  https://ffrt.ru/tournament8938/player/191161
9108 done:  ./data/ffrt/players/ffrt_player_id_191161.txt
9109 processing:  https://ffrt.ru/tournament15032/player/296178
9109 done:  ./data/ffrt/players/ffrt_player_id_296178.txt
9110 processing:  https://ff

9169 done:  ./data/ffrt/players/ffrt_player_id_423859.txt
9170 processing:  https://ffrt.ru/tournament15044/player/306080
9170 done:  ./data/ffrt/players/ffrt_player_id_306080.txt
9171 processing:  https://ffrt.ru/tournament14673/player/206430
9171 done:  ./data/ffrt/players/ffrt_player_id_206430.txt
9172 processing:  https://ffrt.ru/tournament13428/player/362176
9172 done:  ./data/ffrt/players/ffrt_player_id_362176.txt
9173 processing:  https://ffrt.ru/tournament3520/player/193622
9173 done:  ./data/ffrt/players/ffrt_player_id_193622.txt
9174 processing:  https://ffrt.ru/tournament7192/player/166603
9174 done:  ./data/ffrt/players/ffrt_player_id_166603.txt
9175 processing:  https://ffrt.ru/tournament8937/player/147348
9175 done:  ./data/ffrt/players/ffrt_player_id_147348.txt
9176 processing:  https://ffrt.ru/tournament10317/player/149493
9176 done:  ./data/ffrt/players/ffrt_player_id_149493.txt
9177 processing:  https://ffrt.ru/tournament7192/player/288315
9177 done:  ./data/ffrt/play

9237 done:  ./data/ffrt/players/ffrt_player_id_183540.txt
9238 processing:  https://ffrt.ru/tournament3987/player/215270
9238 done:  ./data/ffrt/players/ffrt_player_id_215270.txt
9239 processing:  https://ffrt.ru/tournament15419/player/199981
9239 done:  ./data/ffrt/players/ffrt_player_id_199981.txt
9240 processing:  https://ffrt.ru/tournament8978/player/173914
9240 done:  ./data/ffrt/players/ffrt_player_id_173914.txt
9241 processing:  https://ffrt.ru/tournament13374/player/296275
9241 done:  ./data/ffrt/players/ffrt_player_id_296275.txt
9242 processing:  https://ffrt.ru/tournament12986/player/345893
9242 done:  ./data/ffrt/players/ffrt_player_id_345893.txt
9243 processing:  https://ffrt.ru/tournament13427/player/365318
9243 done:  ./data/ffrt/players/ffrt_player_id_365318.txt
9244 processing:  https://ffrt.ru/tournament14855/player/399176
9244 done:  ./data/ffrt/players/ffrt_player_id_399176.txt
9245 processing:  https://ffrt.ru/tournament9089/player/202904
9245 done:  ./data/ffrt/pla

...

41548 done:  ./data/ffrt/players/ffrt_player_id_307033.txt
41549 processing:  https://ffrt.ru/tournament13521/player/288317
41549 done:  ./data/ffrt/players/ffrt_player_id_288317.txt
41550 processing:  https://ffrt.ru/tournament3189/player/127536
41550 done:  ./data/ffrt/players/ffrt_player_id_127536.txt
41551 processing:  https://ffrt.ru/tournament15131/player/169613
41551 done:  ./data/ffrt/players/ffrt_player_id_169613.txt
41552 processing:  https://ffrt.ru/tournament10176/player/184057
41552 done:  ./data/ffrt/players/ffrt_player_id_184057.txt
41553 processing:  https://ffrt.ru/tournament10176/player/318978
41553 done:  ./data/ffrt/players/ffrt_player_id_318978.txt
41554 processing:  https://ffrt.ru/tournament8980/player/258101
41554 done:  ./data/ffrt/players/ffrt_player_id_258101.txt
41555 processing:  https://ffrt.ru/tournament3189/player/142330
41555 done:  ./data/ffrt/players/ffrt_player_id_142330.txt
41556 processing:  https://ffrt.ru/tournament3405/player/175238
41556 done: 

41615 processing:  https://ffrt.ru/tournament10154/player/174948
41615 done:  ./data/ffrt/players/ffrt_player_id_174948.txt
41616 processing:  https://ffrt.ru/tournament8980/player/256829
41616 done:  ./data/ffrt/players/ffrt_player_id_256829.txt
41617 processing:  https://ffrt.ru/tournament4560/player/120184
41617 done:  ./data/ffrt/players/ffrt_player_id_120184.txt
41618 processing:  https://ffrt.ru/tournament7190/player/141552
41618 done:  ./data/ffrt/players/ffrt_player_id_141552.txt
41619 processing:  https://ffrt.ru/tournament3192/player/169422
41619 done:  ./data/ffrt/players/ffrt_player_id_169422.txt
41620 processing:  https://ffrt.ru/tournament16249/player/361632
41620 done:  ./data/ffrt/players/ffrt_player_id_361632.txt
41621 processing:  https://ffrt.ru/tournament13825/player/247602
41621 done:  ./data/ffrt/players/ffrt_player_id_247602.txt
41622 processing:  https://ffrt.ru/tournament8979/player/295065
41622 done:  ./data/ffrt/players/ffrt_player_id_295065.txt
41623 process

41681 done:  ./data/ffrt/players/ffrt_player_id_174612.txt
41682 processing:  https://ffrt.ru/tournament8931/player/144515
41682 done:  ./data/ffrt/players/ffrt_player_id_144515.txt
41683 processing:  https://ffrt.ru/tournament16667/player/469195
41683 done:  ./data/ffrt/players/ffrt_player_id_469195.txt
41684 processing:  https://ffrt.ru/tournament13446/player/143002
41684 done:  ./data/ffrt/players/ffrt_player_id_143002.txt
41685 processing:  https://ffrt.ru/tournament1887/player/224622
41685 done:  ./data/ffrt/players/ffrt_player_id_224622.txt
41686 processing:  https://ffrt.ru/tournament3986/player/199907
41686 done:  ./data/ffrt/players/ffrt_player_id_199907.txt
41687 processing:  https://ffrt.ru/tournament10176/player/174934
41687 done:  ./data/ffrt/players/ffrt_player_id_174934.txt
41688 processing:  https://ffrt.ru/tournament8980/player/256845
41688 done:  ./data/ffrt/players/ffrt_player_id_256845.txt
41689 processing:  https://ffrt.ru/tournament9094/player/317021
41689 done:  

41748 processing:  https://ffrt.ru/tournament9265/player/308835
41748 done:  ./data/ffrt/players/ffrt_player_id_308835.txt
41749 processing:  https://ffrt.ru/tournament3189/player/115707
41749 done:  ./data/ffrt/players/ffrt_player_id_115707.txt
41750 processing:  https://ffrt.ru/tournament8931/player/142681
41750 done:  ./data/ffrt/players/ffrt_player_id_142681.txt
41751 processing:  https://ffrt.ru/tournament8934/player/105516
41751 done:  ./data/ffrt/players/ffrt_player_id_105516.txt
41752 processing:  https://ffrt.ru/tournament3192/player/146666
41752 done:  ./data/ffrt/players/ffrt_player_id_146666.txt
41753 processing:  https://ffrt.ru/tournament15029/player/403003
41753 done:  ./data/ffrt/players/ffrt_player_id_403003.txt
41754 processing:  https://ffrt.ru/tournament15029/player/185393
41754 done:  ./data/ffrt/players/ffrt_player_id_185393.txt
41755 processing:  https://ffrt.ru/tournament1889/player/136569
41755 done:  ./data/ffrt/players/ffrt_player_id_136569.txt
41756 processi

41814 done:  ./data/ffrt/players/ffrt_player_id_174644.txt
41815 processing:  https://ffrt.ru/tournament13366/player/238006
41815 done:  ./data/ffrt/players/ffrt_player_id_238006.txt
41816 processing:  https://ffrt.ru/tournament7122/player/134354
41816 done:  ./data/ffrt/players/ffrt_player_id_134354.txt
41817 processing:  https://ffrt.ru/tournament8980/player/306141
41817 done:  ./data/ffrt/players/ffrt_player_id_306141.txt


## By single referee

In [13]:
start_index = len(os.listdir(CACHE_PATH_RFRS))
for i_rfr, url_rfr in enumerate(url_rfrs[start_index:]):
    print(i_rfr + start_index, 'processing: ', url_rfr)
    html = get_content(url_rfr, TIMEOUT, PROXIES)
    tmt_id = url_rfr[url_rfr.find('/tournament') + len('/tournament'):url_rfr.find('referee/') - 1]
    rfr_id = url_rfr[url_rfr.find('referee/') + len('referee/'):]
    file_name = '{}{}_referee_id_{}_tournament_id_{}.html'.format(CACHE_PATH_RFRS_RAW, site_name, rfr_id, tmt_id)
    with open(file_name, 'w', encoding='utf-8') as file:
        file.write(str(html))
    with open(file_name, 'r', encoding='utf-8') as file:
        html = file.read()    
    soup = BeautifulSoup(html, 'lxml')
    referee_data = {}
    if soup.find_all('tbody'):
        for tr in soup.find_all('tbody')[0].find_all('tr'):
            referee_data[tr.find('th').text.strip()] = tr.find('td').text.strip()
    if soup.find('div', {'class': 'row referee-card'}):
        for span in soup.find('div', {'class': 'row referee-card'}).find_all('span'):
            txt = span.text.strip()
            referee_data[txt[:txt.find(':')]] = txt[txt.find(':') + 1:].strip()
        games = []
        header = [th.text.strip() for th in soup.find_all('thead')[1].find_all('th')]
        for row in soup.find_all('tbody')[2].find_all('tr'):
            game = {}
            for key, td in zip(header, row.find_all('td')):
                game[key] = ' '.join(td.text.split())
                if td.find_all('a', href=True):
                    for i_href, href in enumerate(td.find_all('a', href=True)):
                        key_href = '{}_href_{}'.format(key, i_href)
                        game[key_href] = href['href']
            games.append(game)
        referee_data['games'] = games 
    #---write to file---
    file_name = '{}{}_referee_id_{}_tournament_id_{}.txt'.format(CACHE_PATH_RFRS, site_name, rfr_id, tmt_id)
    with open(file_name, 'w') as file:
        json.dump(referee_data, file)
    print(i_rfr + start_index, 'done: ', file_name)
    sleep(randint(MIN_TIME_SLEEP, MAX_TIME_SLEEP))

379 processing:  https://ffrt.ru/tournament3529/referee/215426
URLError |  https://ffrt.ru/tournament3529/referee/215426  |  <urlopen error [Errno 11001] getaddrinfo failed>  | counts:  1
URLError |  https://ffrt.ru/tournament3529/referee/215426  |  <urlopen error [Errno 11001] getaddrinfo failed>  | counts:  2
URLError |  https://ffrt.ru/tournament3529/referee/215426  |  <urlopen error [Errno 11001] getaddrinfo failed>  | counts:  3
URLError |  https://ffrt.ru/tournament3529/referee/215426  |  <urlopen error [Errno 11001] getaddrinfo failed>  | counts:  4
URLError |  https://ffrt.ru/tournament3529/referee/215426  |  <urlopen error [Errno 11001] getaddrinfo failed>  | counts:  5
379 done:  ./data/ffrt/referees/ffrt_referee_id_215426_tournament_id_3529.txt
380 processing:  https://ffrt.ru/tournament3529/referee/87878
380 done:  ./data/ffrt/referees/ffrt_referee_id_87878_tournament_id_3529.txt
381 processing:  https://ffrt.ru/tournament7363/referee/87872
381 done:  ./data/ffrt/referees/f

433 processing:  https://ffrt.ru/tournament7363/referee/171967
433 done:  ./data/ffrt/referees/ffrt_referee_id_171967_tournament_id_7363.txt
434 processing:  https://ffrt.ru/tournament13829/referee/215426
434 done:  ./data/ffrt/referees/ffrt_referee_id_215426_tournament_id_13829.txt
435 processing:  https://ffrt.ru/tournament9176/referee/147271
435 done:  ./data/ffrt/referees/ffrt_referee_id_147271_tournament_id_9176.txt
436 processing:  https://ffrt.ru/tournament13830/referee/169211
436 done:  ./data/ffrt/referees/ffrt_referee_id_169211_tournament_id_13830.txt
437 processing:  https://ffrt.ru/tournament3520/referee/101242
437 done:  ./data/ffrt/referees/ffrt_referee_id_101242_tournament_id_3520.txt
438 processing:  https://ffrt.ru/tournament7194/referee/87474
438 done:  ./data/ffrt/referees/ffrt_referee_id_87474_tournament_id_7194.txt
439 processing:  https://ffrt.ru/tournament13818/referee/143498
439 done:  ./data/ffrt/referees/ffrt_referee_id_143498_tournament_id_13818.txt
440 proce

491 done:  ./data/ffrt/referees/ffrt_referee_id_87469_tournament_id_15047.txt
492 processing:  https://ffrt.ru/tournament9173/referee/88152
492 done:  ./data/ffrt/referees/ffrt_referee_id_88152_tournament_id_9173.txt
493 processing:  https://ffrt.ru/tournament3183/referee/87886
493 done:  ./data/ffrt/referees/ffrt_referee_id_87886_tournament_id_3183.txt
494 processing:  https://ffrt.ru/tournament9176/referee/87470
494 done:  ./data/ffrt/referees/ffrt_referee_id_87470_tournament_id_9176.txt
495 processing:  https://ffrt.ru/tournament8937/referee/171486
495 done:  ./data/ffrt/referees/ffrt_referee_id_171486_tournament_id_8937.txt
496 processing:  https://ffrt.ru/tournament8938/referee/87460
496 done:  ./data/ffrt/referees/ffrt_referee_id_87460_tournament_id_8938.txt
497 processing:  https://ffrt.ru/tournament13364/referee/87460
497 done:  ./data/ffrt/referees/ffrt_referee_id_87460_tournament_id_13364.txt
498 processing:  https://ffrt.ru/tournament3640/referee/169079
498 done:  ./data/ffr

550 processing:  https://ffrt.ru/tournament9094/referee/143498
550 done:  ./data/ffrt/referees/ffrt_referee_id_143498_tournament_id_9094.txt
551 processing:  https://ffrt.ru/tournament7193/referee/133019
551 done:  ./data/ffrt/referees/ffrt_referee_id_133019_tournament_id_7193.txt
552 processing:  https://ffrt.ru/tournament9265/referee/218942
552 done:  ./data/ffrt/referees/ffrt_referee_id_218942_tournament_id_9265.txt
553 processing:  https://ffrt.ru/tournament9097/referee/154143
553 done:  ./data/ffrt/referees/ffrt_referee_id_154143_tournament_id_9097.txt
554 processing:  https://ffrt.ru/tournament13825/referee/143498
554 done:  ./data/ffrt/referees/ffrt_referee_id_143498_tournament_id_13825.txt
555 processing:  https://ffrt.ru/tournament13827/referee/147271
555 done:  ./data/ffrt/referees/ffrt_referee_id_147271_tournament_id_13827.txt
556 processing:  https://ffrt.ru/tournament3860/referee/134874
556 done:  ./data/ffrt/referees/ffrt_referee_id_134874_tournament_id_3860.txt
557 proce

608 done:  ./data/ffrt/referees/ffrt_referee_id_125840_tournament_id_9952.txt
609 processing:  https://ffrt.ru/tournament6481/referee/191077
609 done:  ./data/ffrt/referees/ffrt_referee_id_191077_tournament_id_6481.txt
610 processing:  https://ffrt.ru/tournament13591/referee/340446
610 done:  ./data/ffrt/referees/ffrt_referee_id_340446_tournament_id_13591.txt
611 processing:  https://ffrt.ru/tournament10051/referee/87880
611 done:  ./data/ffrt/referees/ffrt_referee_id_87880_tournament_id_10051.txt
612 processing:  https://ffrt.ru/tournament3651/referee/185242
612 done:  ./data/ffrt/referees/ffrt_referee_id_185242_tournament_id_3651.txt
613 processing:  https://ffrt.ru/tournament7122/referee/87880
613 done:  ./data/ffrt/referees/ffrt_referee_id_87880_tournament_id_7122.txt
614 processing:  https://ffrt.ru/tournament3651/referee/87473
614 done:  ./data/ffrt/referees/ffrt_referee_id_87473_tournament_id_3651.txt
615 processing:  https://ffrt.ru/tournament10176/referee/204820
615 done:  ./d

...

2564 processing:  https://ffrt.ru/tournament3526/referee/87466
2564 done:  ./data/ffrt/referees/ffrt_referee_id_87466_tournament_id_3526.txt
2565 processing:  https://ffrt.ru/tournament9173/referee/133019
2565 done:  ./data/ffrt/referees/ffrt_referee_id_133019_tournament_id_9173.txt
2566 processing:  https://ffrt.ru/tournament13446/referee/87462
2566 done:  ./data/ffrt/referees/ffrt_referee_id_87462_tournament_id_13446.txt
2567 processing:  https://ffrt.ru/tournament3986/referee/88715
2567 done:  ./data/ffrt/referees/ffrt_referee_id_88715_tournament_id_3986.txt
2568 processing:  https://ffrt.ru/tournament15118/referee/134873
2568 done:  ./data/ffrt/referees/ffrt_referee_id_134873_tournament_id_15118.txt
2569 processing:  https://ffrt.ru/tournament16159/referee/143498
2569 done:  ./data/ffrt/referees/ffrt_referee_id_143498_tournament_id_16159.txt
2570 processing:  https://ffrt.ru/tournament15320/referee/197181
2570 done:  ./data/ffrt/referees/ffrt_referee_id_197181_tournament_id_15320.t

2621 done:  ./data/ffrt/referees/ffrt_referee_id_143687_tournament_id_10176.txt
2622 processing:  https://ffrt.ru/tournament3192/referee/169079
2622 done:  ./data/ffrt/referees/ffrt_referee_id_169079_tournament_id_3192.txt
2623 processing:  https://ffrt.ru/tournament13829/referee/87458
2623 done:  ./data/ffrt/referees/ffrt_referee_id_87458_tournament_id_13829.txt
2624 processing:  https://ffrt.ru/tournament15118/referee/140815
2624 done:  ./data/ffrt/referees/ffrt_referee_id_140815_tournament_id_15118.txt
2625 processing:  https://ffrt.ru/tournament13829/referee/87886
2625 done:  ./data/ffrt/referees/ffrt_referee_id_87886_tournament_id_13829.txt
2626 processing:  https://ffrt.ru/tournament3526/referee/147271
2626 done:  ./data/ffrt/referees/ffrt_referee_id_147271_tournament_id_3526.txt
2627 processing:  https://ffrt.ru/tournament3860/referee/147271
2627 done:  ./data/ffrt/referees/ffrt_referee_id_147271_tournament_id_3860.txt
2628 processing:  https://ffrt.ru/tournament15122/referee/87

2678 processing:  https://ffrt.ru/tournament13521/referee/124672
2678 done:  ./data/ffrt/referees/ffrt_referee_id_124672_tournament_id_13521.txt
2679 processing:  https://ffrt.ru/tournament13446/referee/215426
2679 done:  ./data/ffrt/referees/ffrt_referee_id_215426_tournament_id_13446.txt
2680 processing:  https://ffrt.ru/tournament3183/referee/87472
2680 done:  ./data/ffrt/referees/ffrt_referee_id_87472_tournament_id_3183.txt
2681 processing:  https://ffrt.ru/tournament9176/referee/101120
2681 done:  ./data/ffrt/referees/ffrt_referee_id_101120_tournament_id_9176.txt
2682 processing:  https://ffrt.ru/tournament3860/referee/125840
2682 done:  ./data/ffrt/referees/ffrt_referee_id_125840_tournament_id_3860.txt
2683 processing:  https://ffrt.ru/tournament13359/referee/101242
2683 done:  ./data/ffrt/referees/ffrt_referee_id_101242_tournament_id_13359.txt
2684 processing:  https://ffrt.ru/tournament7193/referee/197181
2684 done:  ./data/ffrt/referees/ffrt_referee_id_197181_tournament_id_7193

2735 done:  ./data/ffrt/referees/ffrt_referee_id_123098_tournament_id_3651.txt
2736 processing:  https://ffrt.ru/tournament3190/referee/87872
2736 done:  ./data/ffrt/referees/ffrt_referee_id_87872_tournament_id_3190.txt
2737 processing:  https://ffrt.ru/tournament13850/referee/185602
2737 done:  ./data/ffrt/referees/ffrt_referee_id_185602_tournament_id_13850.txt
2738 processing:  https://ffrt.ru/tournament9160/referee/185602
2738 done:  ./data/ffrt/referees/ffrt_referee_id_185602_tournament_id_9160.txt
2739 processing:  https://ffrt.ru/tournament8931/referee/87880
2739 done:  ./data/ffrt/referees/ffrt_referee_id_87880_tournament_id_8931.txt
2740 processing:  https://ffrt.ru/tournament3528/referee/185242
2740 done:  ./data/ffrt/referees/ffrt_referee_id_185242_tournament_id_3528.txt
2741 processing:  https://ffrt.ru/tournament3520/referee/87886
2741 done:  ./data/ffrt/referees/ffrt_referee_id_87886_tournament_id_3520.txt
2742 processing:  https://ffrt.ru/tournament13825/referee/179157
27

2793 processing:  https://ffrt.ru/tournament3183/referee/87471
2793 done:  ./data/ffrt/referees/ffrt_referee_id_87471_tournament_id_3183.txt
2794 processing:  https://ffrt.ru/tournament1641/referee/101147
2794 done:  ./data/ffrt/referees/ffrt_referee_id_101147_tournament_id_1641.txt
2795 processing:  https://ffrt.ru/tournament8949/referee/143687
2795 done:  ./data/ffrt/referees/ffrt_referee_id_143687_tournament_id_8949.txt
2796 processing:  https://ffrt.ru/tournament10051/referee/125840
2796 done:  ./data/ffrt/referees/ffrt_referee_id_125840_tournament_id_10051.txt
2797 processing:  https://ffrt.ru/tournament1755/referee/133019
2797 done:  ./data/ffrt/referees/ffrt_referee_id_133019_tournament_id_1755.txt
2798 processing:  https://ffrt.ru/tournament13827/referee/133020
2798 done:  ./data/ffrt/referees/ffrt_referee_id_133020_tournament_id_13827.txt
2799 processing:  https://ffrt.ru/tournament10075/referee/252787
2799 done:  ./data/ffrt/referees/ffrt_referee_id_252787_tournament_id_10075

## By single official

In [19]:
start_index = len(os.listdir(CACHE_PATH_OFLS))
for i_ofl, url_ofl in enumerate(url_ofls[start_index:]):    
    print(i_ofl + start_index, 'processing: ', url_ofl)
    html = get_content(url_ofl, TIMEOUT, PROXIES)
    tmt_id = url_ofl[url_ofl.find('/tournament') + len('/tournament'):url_ofl.find('official/') - 1]
    ofl_id = url_ofl[url_ofl.find('official/') + len('official/'):]
    file_name = '{}{}_official_id_{}_tournament_id_{}.html'.format(CACHE_PATH_OFLS_RAW, site_name, ofl_id, tmt_id)
    with open(file_name, 'w', encoding='utf-8') as file:
        file.write(str(html))
    with open(file_name, 'r', encoding='utf-8') as file:
        html = file.read()    
    soup = BeautifulSoup(html, 'lxml')
    ofl_data = {}
    if soup.find_all('table', {'class': "table"}):
        for tr in soup.find_all('table', {'class': "table"})[0].find_all('tr'):
            ofl_data[tr.find('th').text.strip()] = tr.find('td').text.strip()
    if soup.find_all('div', {'class': "col-xs-9"}):
        if len(soup.find_all('div', {'class': "col-xs-9"})) >= 2:
            for span in soup.find_all('div', {'class': "col-xs-9"})[1].find_all('span'):
                txt = span.text.strip()
                if ': ' in txt:
                    ofl_data[txt[:txt.find(':')]] = txt[txt.find(':') + 1:].strip()
    games = []
    if soup.find_all('table', {'class': "table table-striped"}):
        header = [th.text.strip() for th in soup.find_all('table', {'class': "table table-striped"})[0].find_all('th')]
    if soup.find_all('table', {'class': "table table-striped"}):
        for row in soup.find_all('table', {'class': "table table-striped"})[0].find_all('tr'):
            game = {}
            for key, td in zip(header, row.find_all('td')):
                game[key] = ' '.join(td.text.split())
                if td.find_all('a', href=True):
                    for i_href, href in enumerate(td.find_all('a', href=True)):
                        key_href = '{}_href_{}'.format(key, i_href)
                        game[key_href] = href['href']
            if game:
                games.append(game) 
    ofl_data['games'] = games 
    #---write to file---
    file_name = '{}{}_official_id_{}_tournament_id_{}.txt'.format(CACHE_PATH_OFLS, site_name, ofl_id, tmt_id)
    with open(file_name, 'w') as file:
        json.dump(ofl_data, file)
    print(i_ofl + start_index, 'done: ', file_name)
    sleep(randint(MIN_TIME_SLEEP, MAX_TIME_SLEEP))

81 processing:  https://ffrt.ru/tournament1639/official/149003
81 done:  ./data/ffrt/officials/ffrt_official_id_149003_tournament_id_1639.txt
82 processing:  https://ffrt.ru/tournament15030/official/230743
82 done:  ./data/ffrt/officials/ffrt_official_id_230743_tournament_id_15030.txt
83 processing:  https://ffrt.ru/tournament6798/official/183660
83 done:  ./data/ffrt/officials/ffrt_official_id_183660_tournament_id_6798.txt
84 processing:  https://ffrt.ru/tournament3344/official/174378
84 done:  ./data/ffrt/officials/ffrt_official_id_174378_tournament_id_3344.txt
85 processing:  https://ffrt.ru/tournament1639/official/87875
85 done:  ./data/ffrt/officials/ffrt_official_id_87875_tournament_id_1639.txt
86 processing:  https://ffrt.ru/tournament1639/official/148992
86 done:  ./data/ffrt/officials/ffrt_official_id_148992_tournament_id_1639.txt
87 processing:  https://ffrt.ru/tournament9176/official/168718
87 done:  ./data/ffrt/officials/ffrt_official_id_168718_tournament_id_9176.txt
88 pro

138 processing:  https://ffrt.ru/tournament8952/official/183681
138 done:  ./data/ffrt/officials/ffrt_official_id_183681_tournament_id_8952.txt
139 processing:  https://ffrt.ru/tournament13689/official/201839
139 done:  ./data/ffrt/officials/ffrt_official_id_201839_tournament_id_13689.txt
140 processing:  https://ffrt.ru/tournament14673/official/359740
140 done:  ./data/ffrt/officials/ffrt_official_id_359740_tournament_id_14673.txt
141 processing:  https://ffrt.ru/tournament9097/official/294376
141 done:  ./data/ffrt/officials/ffrt_official_id_294376_tournament_id_9097.txt
142 processing:  https://ffrt.ru/tournament10375/official/151450
142 done:  ./data/ffrt/officials/ffrt_official_id_151450_tournament_id_10375.txt
143 processing:  https://ffrt.ru/tournament3988/official/203986
143 done:  ./data/ffrt/officials/ffrt_official_id_203986_tournament_id_3988.txt
144 processing:  https://ffrt.ru/tournament15419/official/237426
144 done:  ./data/ffrt/officials/ffrt_official_id_237426_tourname

195 processing:  https://ffrt.ru/tournament16667/official/469149
195 done:  ./data/ffrt/officials/ffrt_official_id_469149_tournament_id_16667.txt
196 processing:  https://ffrt.ru/tournament3526/official/101230
196 done:  ./data/ffrt/officials/ffrt_official_id_101230_tournament_id_3526.txt
197 processing:  https://ffrt.ru/tournament15118/official/109600
197 done:  ./data/ffrt/officials/ffrt_official_id_109600_tournament_id_15118.txt
198 processing:  https://ffrt.ru/tournament3183/official/149689
198 done:  ./data/ffrt/officials/ffrt_official_id_149689_tournament_id_3183.txt
199 processing:  https://ffrt.ru/tournament15420/official/423864
199 done:  ./data/ffrt/officials/ffrt_official_id_423864_tournament_id_15420.txt
200 processing:  https://ffrt.ru/tournament15031/official/174655
200 done:  ./data/ffrt/officials/ffrt_official_id_174655_tournament_id_15031.txt
201 processing:  https://ffrt.ru/tournament3526/official/101226
201 done:  ./data/ffrt/officials/ffrt_official_id_101226_tournam

252 processing:  https://ffrt.ru/tournament3860/official/133710
252 done:  ./data/ffrt/officials/ffrt_official_id_133710_tournament_id_3860.txt
253 processing:  https://ffrt.ru/tournament7122/official/124410
253 done:  ./data/ffrt/officials/ffrt_official_id_124410_tournament_id_7122.txt
254 processing:  https://ffrt.ru/tournament4414/official/174503
254 done:  ./data/ffrt/officials/ffrt_official_id_174503_tournament_id_4414.txt
255 processing:  https://ffrt.ru/tournament14958/official/87716
255 done:  ./data/ffrt/officials/ffrt_official_id_87716_tournament_id_14958.txt
256 processing:  https://ffrt.ru/tournament15118/official/109601
256 done:  ./data/ffrt/officials/ffrt_official_id_109601_tournament_id_15118.txt
257 processing:  https://ffrt.ru/tournament15118/official/204680
257 done:  ./data/ffrt/officials/ffrt_official_id_204680_tournament_id_15118.txt
258 processing:  https://ffrt.ru/tournament15420/official/119977
258 done:  ./data/ffrt/officials/ffrt_official_id_119977_tournament

309 processing:  https://ffrt.ru/tournament15049/official/200553
309 done:  ./data/ffrt/officials/ffrt_official_id_200553_tournament_id_15049.txt
310 processing:  https://ffrt.ru/tournament3894/official/109547
310 done:  ./data/ffrt/officials/ffrt_official_id_109547_tournament_id_3894.txt
311 processing:  https://ffrt.ru/tournament8979/official/168718
311 done:  ./data/ffrt/officials/ffrt_official_id_168718_tournament_id_8979.txt
312 processing:  https://ffrt.ru/tournament10375/official/151449
312 done:  ./data/ffrt/officials/ffrt_official_id_151449_tournament_id_10375.txt
313 processing:  https://ffrt.ru/tournament6887/official/190548
313 done:  ./data/ffrt/officials/ffrt_official_id_190548_tournament_id_6887.txt
314 processing:  https://ffrt.ru/tournament7122/official/223902
314 done:  ./data/ffrt/officials/ffrt_official_id_223902_tournament_id_7122.txt
315 processing:  https://ffrt.ru/tournament16159/official/183515
315 done:  ./data/ffrt/officials/ffrt_official_id_183515_tournament

...

2505 processing:  https://ffrt.ru/tournament15203/official/109600
2505 done:  ./data/ffrt/officials/ffrt_official_id_109600_tournament_id_15203.txt
2506 processing:  https://ffrt.ru/tournament3640/official/174127
2506 done:  ./data/ffrt/officials/ffrt_official_id_174127_tournament_id_3640.txt
2507 processing:  https://ffrt.ru/tournament15029/official/134879
2507 done:  ./data/ffrt/officials/ffrt_official_id_134879_tournament_id_15029.txt
2508 processing:  https://ffrt.ru/tournament3183/official/109547
2508 done:  ./data/ffrt/officials/ffrt_official_id_109547_tournament_id_3183.txt
2509 processing:  https://ffrt.ru/tournament15122/official/177545
2509 done:  ./data/ffrt/officials/ffrt_official_id_177545_tournament_id_15122.txt
2510 processing:  https://ffrt.ru/tournament15122/official/189324
2510 done:  ./data/ffrt/officials/ffrt_official_id_189324_tournament_id_15122.txt
2511 processing:  https://ffrt.ru/tournament13830/official/146752
2511 done:  ./data/ffrt/officials/ffrt_official_id

2561 processing:  https://ffrt.ru/tournament3192/official/177545
2561 done:  ./data/ffrt/officials/ffrt_official_id_177545_tournament_id_3192.txt
2562 processing:  https://ffrt.ru/tournament1753/official/105371
2562 done:  ./data/ffrt/officials/ffrt_official_id_105371_tournament_id_1753.txt
2563 processing:  https://ffrt.ru/tournament7054/official/403209
2563 done:  ./data/ffrt/officials/ffrt_official_id_403209_tournament_id_7054.txt
2564 processing:  https://ffrt.ru/tournament13223/official/303390
2564 done:  ./data/ffrt/officials/ffrt_official_id_303390_tournament_id_13223.txt
2565 processing:  https://ffrt.ru/tournament3989/official/169474
2565 done:  ./data/ffrt/officials/ffrt_official_id_169474_tournament_id_3989.txt
2566 processing:  https://ffrt.ru/tournament1639/official/148990
2566 done:  ./data/ffrt/officials/ffrt_official_id_148990_tournament_id_1639.txt
2567 processing:  https://ffrt.ru/tournament9176/official/183676
2567 done:  ./data/ffrt/officials/ffrt_official_id_183676

2617 processing:  https://ffrt.ru/tournament15030/official/175202
2617 done:  ./data/ffrt/officials/ffrt_official_id_175202_tournament_id_15030.txt
2618 processing:  https://ffrt.ru/tournament10374/official/335202
2618 done:  ./data/ffrt/officials/ffrt_official_id_335202_tournament_id_10374.txt
2619 processing:  https://ffrt.ru/tournament13816/official/175213
2619 done:  ./data/ffrt/officials/ffrt_official_id_175213_tournament_id_13816.txt
2620 processing:  https://ffrt.ru/tournament9089/official/200554
2620 done:  ./data/ffrt/officials/ffrt_official_id_200554_tournament_id_9089.txt
2621 processing:  https://ffrt.ru/tournament3860/official/101203
2621 done:  ./data/ffrt/officials/ffrt_official_id_101203_tournament_id_3860.txt
2622 processing:  https://ffrt.ru/tournament13351/official/174503
2622 done:  ./data/ffrt/officials/ffrt_official_id_174503_tournament_id_13351.txt
2623 processing:  https://ffrt.ru/tournament8949/official/183660
2623 done:  ./data/ffrt/officials/ffrt_official_id_

2673 processing:  https://ffrt.ru/tournament15044/official/101043
2673 done:  ./data/ffrt/officials/ffrt_official_id_101043_tournament_id_15044.txt
2674 processing:  https://ffrt.ru/tournament15129/official/109595
2674 done:  ./data/ffrt/officials/ffrt_official_id_109595_tournament_id_15129.txt
2675 processing:  https://ffrt.ru/tournament13521/official/219080
2675 done:  ./data/ffrt/officials/ffrt_official_id_219080_tournament_id_13521.txt
2676 processing:  https://ffrt.ru/tournament3343/official/146867
2676 done:  ./data/ffrt/officials/ffrt_official_id_146867_tournament_id_3343.txt
2677 processing:  https://ffrt.ru/tournament9173/official/133710
2677 done:  ./data/ffrt/officials/ffrt_official_id_133710_tournament_id_9173.txt
2678 processing:  https://ffrt.ru/tournament9173/official/133712
2678 done:  ./data/ffrt/officials/ffrt_official_id_133712_tournament_id_9173.txt
2679 processing:  https://ffrt.ru/tournament13374/official/173902
2679 done:  ./data/ffrt/officials/ffrt_official_id_1

2729 processing:  https://ffrt.ru/tournament3652/official/108733
2729 done:  ./data/ffrt/officials/ffrt_official_id_108733_tournament_id_3652.txt
2730 processing:  https://ffrt.ru/tournament3189/official/141817
2730 done:  ./data/ffrt/officials/ffrt_official_id_141817_tournament_id_3189.txt
2731 processing:  https://ffrt.ru/tournament9095/official/101226
2731 done:  ./data/ffrt/officials/ffrt_official_id_101226_tournament_id_9095.txt
2732 processing:  https://ffrt.ru/tournament7122/official/170050
2732 done:  ./data/ffrt/officials/ffrt_official_id_170050_tournament_id_7122.txt
2733 processing:  https://ffrt.ru/tournament3529/official/186280
2733 done:  ./data/ffrt/officials/ffrt_official_id_186280_tournament_id_3529.txt
2734 processing:  https://ffrt.ru/tournament7122/official/134999
2734 done:  ./data/ffrt/officials/ffrt_official_id_134999_tournament_id_7122.txt
2735 processing:  https://ffrt.ru/tournament9173/official/109600
2735 done:  ./data/ffrt/officials/ffrt_official_id_109600_t